In [2]:
import tensorflow as tf
import pandas as pd
import numpy as np

tf.logging.set_verbosity(tf.logging.INFO)

In [4]:
# Load training and eval data
mnist = tf.contrib.learn.datasets.load_dataset("mnist")
train_data = mnist.train.images  # Returns np.array
train_labels = np.asarray(mnist.train.labels, dtype=np.int32)
eval_data = mnist.test.images  # Returns np.array
eval_labels = np.asarray(mnist.test.labels, dtype=np.int32)

Instructions for updating:
Use the retry module or similar alternatives.
Instructions for updating:
Please use tf.data.
Instructions for updating:
Please use alternatives such as official/mnist/dataset.py from tensorflow/models.
Instructions for updating:
Please use alternatives such as official/mnist/dataset.py from tensorflow/models.
Instructions for updating:
Please write your own downloading logic.
Instructions for updating:
Please use urllib or similar directly.
Successfully downloaded train-images-idx3-ubyte.gz 9912422 bytes.
Instructions for updating:
Please use tf.data to implement this functionality.
Extracting MNIST-data\train-images-idx3-ubyte.gz
Successfully downloaded train-labels-idx1-ubyte.gz 28881 bytes.
Instructions for updating:
Please use tf.data to implement this functionality.
Extracting MNIST-data\train-labels-idx1-ubyte.gz
Successfully downloaded t10k-images-idx3-ubyte.gz 1648877 bytes.
Extracting MNIST-data\t10k-images-idx3-ubyte.gz
Successfully downloaded t10k-

In [11]:
def cnn_model_fn(features, labels, mode):
    input_layer = tf.reshape(features["x"], [-1, 28, 28, 1]) #images 28x28x1(black)
    conv1 = tf.layers.conv2d(inputs=input_layer, filters=32, kernel_size=[5,5], padding='same', activation=tf.nn.relu)
    # 32 5x5 convs - 28x28x32
    pooling1 = tf.layers.max_pooling2d(inputs=conv1, pool_size=[2,2], strides=2) #max pooling on 4 bloack(2x2), no overlap, 14x14x32
    conv2 = tf.layers.conv2d(inputs=pooling1, filters=64, kernel_size=[5,5], padding='same', activation=tf.nn.relu)
    #14x14x64
    pooling2 = tf.layers.max_pooling2d(inputs=conv2, pool_size=[2,2], strides=2) #max pooling on 4 bloack(2x2), no overlap, 7x7x64
    flattened = tf.reshape(pooling2, [-1, 7 * 7 * 64])
    dense1 = tf.layers.dense(inputs=flattened, units=1024, activation=tf.nn.relu)
    dropout1 = tf.layers.dropout(inputs=dense1, rate=0.4, training=(mode == tf.estimator.ModeKeys.TRAIN))
    output_layer = tf.layers.dense(inputs=dropout1, units= 10, activation=None) #logit
    
    predictions = {
      # Generate predictions (for PREDICT and EVAL mode)
      "classes": tf.argmax(input=output_layer, axis=1),
      # Add `softmax_tensor` to the graph. It is used for PREDICT and by the
      # `logging_hook`.
      "probabilities": tf.nn.softmax(output_layer, name="softmax_tensor")
      }
    if mode == tf.estimator.ModeKeys.PREDICT:
        return tf.estimator.EstimatorSpec(mode=mode, predictions=predictions)

    # Calculate Loss (for both TRAIN and EVAL modes)
    loss = tf.losses.sparse_softmax_cross_entropy(labels=labels, logits=output_layer)

    # Configure the Training Op (for TRAIN mode)
    if mode == tf.estimator.ModeKeys.TRAIN:
        optimizer = tf.train.GradientDescentOptimizer(learning_rate=0.001)
        train_op = optimizer.minimize(
            loss=loss,
            global_step=tf.train.get_global_step())
        return tf.estimator.EstimatorSpec(mode=mode, loss=loss, train_op=train_op)

    # Add evaluation metrics (for EVAL mode)
    eval_metric_ops = {
      "accuracy": tf.metrics.accuracy(
          labels=labels, predictions=predictions["classes"])}
    return tf.estimator.EstimatorSpec(
      mode=mode, loss=loss, eval_metric_ops=eval_metric_ops)

In [12]:
mnist_classifier = tf.estimator.Estimator(
      model_fn=cnn_model_fn, model_dir="/tmp/mnist_convnet_model")

# Set up logging for predictions
# Log the values in the "Softmax" tensor with label "probabilities"
tensors_to_log = {"probabilities": "softmax_tensor"}
logging_hook = tf.train.LoggingTensorHook(
    tensors=tensors_to_log, every_n_iter=50)

# Train the model
train_input_fn = tf.estimator.inputs.numpy_input_fn(
      x={"x": train_data},
      y=train_labels,
      batch_size=100,
      num_epochs=None,
      shuffle=True)
mnist_classifier.train(
      input_fn=train_input_fn,
      steps=20000,
      hooks=[logging_hook])

INFO:tensorflow:Using default config.
INFO:tensorflow:Using config: {'_model_dir': '/tmp/mnist_convnet_model', '_tf_random_seed': None, '_save_summary_steps': 100, '_save_checkpoints_steps': None, '_save_checkpoints_secs': 600, '_session_config': None, '_keep_checkpoint_max': 5, '_keep_checkpoint_every_n_hours': 10000, '_log_step_count_steps': 100, '_service': None, '_cluster_spec': <tensorflow.python.training.server_lib.ClusterSpec object at 0x000002270023F160>, '_task_type': 'worker', '_task_id': 0, '_global_id_in_cluster': 0, '_master': '', '_evaluation_master': '', '_is_chief': True, '_num_ps_replicas': 0, '_num_worker_replicas': 1}
INFO:tensorflow:Calling model_fn.
INFO:tensorflow:Done calling model_fn.
INFO:tensorflow:Create CheckpointSaverHook.
INFO:tensorflow:Graph was finalized.
INFO:tensorflow:Running local_init_op.
INFO:tensorflow:Done running local_init_op.
INFO:tensorflow:Saving checkpoints for 1 into /tmp/mnist_convnet_model\model.ckpt.
INFO:tensorflow:probabilities = [[0

INFO:tensorflow:loss = 2.3221402, step = 1
INFO:tensorflow:probabilities = [[0.10407901 0.09723012 0.10000958 0.09695229 0.09171068 0.09766217
  0.09313861 0.09419908 0.10678232 0.11823611]
 [0.10279347 0.10422048 0.09726189 0.10148314 0.0953385  0.09375068
  0.100269   0.10064906 0.10054434 0.10368947]
 [0.10975342 0.09333004 0.09874982 0.08281185 0.09031066 0.0932923
  0.10900345 0.10106515 0.1098232  0.11186021]
 [0.11976719 0.10424878 0.08438849 0.09305575 0.1061189  0.09094589
  0.09354889 0.10208082 0.10486846 0.10097684]
 [0.10847735 0.09713921 0.09836183 0.10238068 0.10050634 0.09436354
  0.0907644  0.10754472 0.09759585 0.10286601]
 [0.1012861  0.10908667 0.09223707 0.09051177 0.09279305 0.10344632
  0.09569853 0.09703296 0.11865646 0.099251  ]
 [0.10161904 0.10098325 0.09578291 0.09130778 0.09390797 0.09292889
  0.10334489 0.09541325 0.11177427 0.11293778]
 [0.11272522 0.0988448  0.09094962 0.09725399 0.09958404 0.09837963
  0.09935752 0.09599349 0.09478013 0.11213154]
 [0.09

INFO:tensorflow:global_step/sec: 7.78325
INFO:tensorflow:probabilities = [[0.12559927 0.08931873 0.08321316 0.09617671 0.1078654  0.08351763
  0.10047399 0.1046318  0.10289288 0.10631038]
 [0.11980317 0.10211173 0.08419191 0.11066999 0.10281346 0.09228721
  0.09052317 0.08739619 0.10608587 0.10411735]
 [0.11286329 0.08885261 0.08379629 0.09368765 0.10217287 0.09310512
  0.10188515 0.10077781 0.11182046 0.11103871]
 [0.10883038 0.1005915  0.0940319  0.10655095 0.09276082 0.10020288
  0.09306575 0.10198696 0.10250553 0.09947332]
 [0.10794503 0.10199808 0.08857599 0.09924233 0.11091436 0.09558864
  0.09539104 0.0930718  0.10122485 0.10604794]
 [0.13746524 0.09724933 0.08726334 0.10295669 0.0853484  0.08393925
  0.10455179 0.10466696 0.09404569 0.10251323]
 [0.10546276 0.10297258 0.08864825 0.0987079  0.09465419 0.10333766
  0.09215473 0.09999629 0.11078043 0.10328521]
 [0.10399664 0.10542826 0.09826058 0.09025454 0.09649232 0.09471382
  0.10130925 0.10497244 0.10066292 0.10390916]
 [0.112

INFO:tensorflow:loss = 2.2813754, step = 101 (12.850 sec)
INFO:tensorflow:probabilities = [[0.10409148 0.10709903 0.0867505  0.10411755 0.09710693 0.09655417
  0.10081685 0.09202419 0.11555287 0.09588638]
 [0.11921555 0.09948239 0.08484275 0.10158707 0.09433729 0.09525506
  0.10817959 0.08928853 0.09599928 0.11181243]
 [0.11233221 0.09288905 0.097247   0.09586034 0.10102838 0.09008088
  0.11027581 0.09959169 0.09215015 0.10854454]
 [0.11781259 0.09359734 0.08834131 0.08702009 0.10267878 0.09329359
  0.10250022 0.0936711  0.11542993 0.10565498]
 [0.11559164 0.10248142 0.08219136 0.09552362 0.09682425 0.09488297
  0.10008484 0.09316216 0.12169283 0.09756491]
 [0.13258913 0.09101341 0.09501036 0.09685215 0.097679   0.09946671
  0.0995151  0.08435654 0.09194978 0.11156774]
 [0.09594136 0.09691128 0.09216025 0.09904412 0.10906246 0.08971891
  0.08975571 0.09783296 0.10624416 0.12332876]
 [0.1009906  0.0867549  0.09709742 0.10634742 0.11294977 0.0968385
  0.0846497  0.08792008 0.10814177 0.1

INFO:tensorflow:global_step/sec: 7.87417
INFO:tensorflow:probabilities = [[0.10263095 0.10399252 0.08768222 0.11178982 0.10038126 0.09759
  0.08855386 0.09693958 0.10342332 0.10701646]
 [0.13486324 0.09339885 0.08270779 0.09390266 0.0949411  0.09974589
  0.10711854 0.08648473 0.10308112 0.10375606]
 [0.10431372 0.11163189 0.0943231  0.09642575 0.09367661 0.09848735
  0.09783651 0.09909609 0.10604671 0.09816229]
 [0.10115504 0.10405909 0.0994919  0.08965294 0.106132   0.09444361
  0.10693475 0.09057505 0.09837828 0.10917738]
 [0.12147544 0.09509435 0.09894002 0.08895272 0.09893321 0.08581125
  0.11068495 0.08948629 0.10301873 0.10760306]
 [0.10760125 0.10337397 0.08466223 0.10344512 0.09204167 0.09173032
  0.09777096 0.09429936 0.11415929 0.11091579]
 [0.09948797 0.10132229 0.09911931 0.10478644 0.09091045 0.10283097
  0.11037978 0.09624983 0.07667461 0.11823827]
 [0.10838372 0.10248505 0.09469342 0.09922585 0.10355782 0.08470383
  0.10807363 0.08539183 0.11255746 0.10092733]
 [0.125226

...

INFO:tensorflow:global_step/sec: 7.36561
INFO:tensorflow:probabilities = [[0.00000065 0.0000457  0.00006642 0.00114521 0.01604745 0.00044634
  0.0000003  0.00133854 0.00186041 0.97904897]
 [0.00000052 0.00000007 0.00000348 0.0000073  0.00000001 0.00000199
  0.         0.99990857 0.000002   0.00007603]
 [0.0000457  0.00001952 0.00076682 0.00004098 0.99214023 0.00007147
  0.00086834 0.00225343 0.0003269  0.00346657]
 [0.0000006  0.99911934 0.0002404  0.00001922 0.00000208 0.0000087
  0.00012662 0.00000817 0.00047381 0.00000119]
 [0.00027805 0.00000525 0.00005598 0.00002034 0.00000643 0.0002889
  0.9988846  0.00000155 0.00045797 0.00000091]
 [0.00000033 0.00353488 0.9962237  0.00017522 0.00000004 0.00000268
  0.00000115 0.00001292 0.00004865 0.0000003 ]
 [0.00016228 0.0003112  0.00007679 0.87031144 0.00000046 0.12888762
  0.00000373 0.00000181 0.00013063 0.0001141 ]
 [0.00115126 0.00002913 0.00102295 0.00072079 0.16937974 0.1793299
  0.00000947 0.32171223 0.10620433 0.22044015]
 [0.999804

INFO:tensorflow:loss = 0.08734933, step = 19801 (13.576 sec)
INFO:tensorflow:probabilities = [[0.00000014 0.01750496 0.9797834  0.00196361 0.00000019 0.00000155
  0.00000018 0.00027585 0.00046763 0.00000232]
 [0.00027187 0.0058809  0.8446857  0.00463282 0.10890983 0.02482366
  0.00261556 0.00183038 0.00253464 0.00381463]
 [0.00000001 0.00000016 0.00000206 0.9999285  0.00000008 0.00002423
  0.         0.00000159 0.00003588 0.00000754]
 [0.         0.00000011 0.00000296 0.0000002  0.9996811  0.00000029
  0.00000202 0.00000141 0.00014651 0.00016553]
 [0.0000477  0.0000008  0.00001687 0.00393767 0.         0.99583685
  0.00000117 0.00000024 0.0001584  0.00000033]
 [0.00003159 0.00000062 0.9989304  0.00100946 0.00000043 0.00000037
  0.00000484 0.00000003 0.00002146 0.00000084]
 [0.00000082 0.00001434 0.00002965 0.0009174  0.9955023  0.00001478
  0.00001474 0.00042054 0.00071795 0.00236742]
 [0.00002381 0.000003   0.00085896 0.9669912  0.00000005 0.01867934
  0.00000308 0.00000003 0.01343758

INFO:tensorflow:global_step/sec: 7.49262
INFO:tensorflow:probabilities = [[0.00010154 0.00022714 0.00000379 0.00028742 0.00000373 0.998042
  0.00000771 0.00013331 0.00117514 0.00001815]
 [0.00020377 0.00025716 0.00126794 0.97269654 0.00001528 0.00299315
  0.00001576 0.00001598 0.02201664 0.00051772]
 [0.00001502 0.9654008  0.0006617  0.0043859  0.00013951 0.00064712
  0.00005374 0.00490026 0.02281204 0.00098398]
 [0.00011073 0.00000764 0.00111439 0.00001358 0.00025855 0.00272008
  0.9950576  0.00000002 0.00071511 0.00000224]
 [0.00000054 0.00000023 0.00000007 0.00003504 0.00000192 0.00013618
  0.         0.9880184  0.0000013  0.01180633]
 [0.00000027 0.00016431 0.98883784 0.00105763 0.00140085 0.00225519
  0.00116146 0.00365098 0.00140197 0.00006965]
 [0.00000113 0.9964635  0.00047692 0.00016077 0.00002217 0.00002252
  0.00001126 0.00175549 0.00102542 0.00006098]
 [0.00046673 0.995852   0.00122281 0.00014134 0.00000443 0.0000859
  0.00054345 0.00012178 0.00154952 0.00001193]
 [0.001352

INFO:tensorflow:loss = 0.17860895, step = 19901 (13.355 sec)
INFO:tensorflow:probabilities = [[0.00174545 0.00000155 0.00000246 0.00002353 0.00004013 0.00108097
  0.00000162 0.98925376 0.00000569 0.00784483]
 [0.00000004 0.00000127 0.00649964 0.99324703 0.         0.0000005
  0.         0.00000012 0.00025075 0.00000064]
 [0.0000065  0.         0.00000005 0.00000486 0.00000113 0.00000146
  0.         0.9961653  0.00000701 0.00381375]
 [0.9989691  0.00000031 0.00008901 0.00001375 0.00000348 0.0000172
  0.00012331 0.00000295 0.00052086 0.00026017]
 [0.00001774 0.9970516  0.00067703 0.0001387  0.00010715 0.00000667
  0.00011738 0.00073477 0.00111895 0.00002992]
 [0.9989956  0.00000044 0.00035079 0.00001092 0.00001349 0.0000028
  0.00024235 0.0000049  0.00022237 0.00015623]
 [0.00153113 0.00000004 0.00000041 0.00007863 0.00004499 0.9957598
  0.00029481 0.00000148 0.00213125 0.0001575 ]
 [0.00000017 0.00002163 0.00002396 0.9990706  0.00000013 0.00007626
  0.00000001 0.00000026 0.00079645 0.0

INFO:tensorflow:Saving checkpoints for 20000 into /tmp/mnist_convnet_model\model.ckpt.
INFO:tensorflow:Loss for final step: 0.26193678.


In [13]:
# Evaluate the model and print results
eval_input_fn = tf.estimator.inputs.numpy_input_fn(
      x={"x": eval_data},
      y=eval_labels,
      num_epochs=1,
      shuffle=False)
eval_results = mnist_classifier.evaluate(input_fn=eval_input_fn)
print(eval_results)

INFO:tensorflow:Calling model_fn.
INFO:tensorflow:Done calling model_fn.
INFO:tensorflow:Starting evaluation at 2018-05-12-12:30:59
INFO:tensorflow:Graph was finalized.
INFO:tensorflow:Restoring parameters from /tmp/mnist_convnet_model\model.ckpt-20000
INFO:tensorflow:Running local_init_op.
INFO:tensorflow:Done running local_init_op.
INFO:tensorflow:Finished evaluation at 2018-05-12-12:31:03
INFO:tensorflow:Saving dict for global step 20000: accuracy = 0.9682, global_step = 20000, loss = 0.103271976
{'accuracy': 0.9682, 'loss': 0.103271976, 'global_step': 20000}
